# Coursework 2
## Final question

$$
    f(x, y) = \sin\left(\frac{1}{2}x^2 - \frac{1}{4}y ^ 2 + 3\right) \cos(2x + 1 - \exp(y)) 
$$

Optimisation procedures are ubiquitous in machine learning models that depend on the maximisation of a likelihood function.

In [122]:
using Plots
using LaTeXStrings
using ForwardDiff

In [256]:
new = [CartesianIndex()]

1-element Array{CartesianIndex{0},1}:
 CartesianIndex()

In [417]:
function plot_path!(hist)
    plot!(eachcol(hist)..., linewidth=2, color=:red)
    scatter!(hist[begin, [begin]], hist[begin, [end]], color=:red, legend=nothing)
end

plot_path! (generic function with 1 method)

In [124]:
function f(X)
    x, y = X
    sin(x ^ 2 / 2 - y ^ 2 /  4 + 3) * cos(2x + 1 - exp(y))
end

∇f = X -> ForwardDiff.gradient(f, X);

In [367]:
xyrange = -5:0.01:1.5
Z = map(X -> f(X[2], X[1]), Base.product(xyrange, xyrange));

## Plain gradient descent

In [368]:
nits = 5_000
X0 = [1, -0.5]
X0 = [0, 0]
X_hist = zeros(nits, 2)
X_hist[begin, :] = X0;

In [369]:
α = 0.1

for i=2:nits
    X0 -= α * ∇f(X0)
    X_hist[i, :] = X0
end

In [419]:
function check_convergence(f, X_hist, maxit; rtol=1e-7)
    converge = false
    nits = size(X_hist)[begin]
    if nits <= 2
        return converge
    end
    
    X_end = X_hist[end, :]
    X_begin = X_hist[end-1, :]
    
    f_end = f(X_end...)
    f_begin = f(X_begin...)
    
    if nits >= maxit
        @warn "Procedure did not converge"
        converge = true
    elseif f_end == f_begin
        @warn "No change observed"
        converge = true
    elseif abs(f_end / f_begin - 1) <= rtol
        converge = true
    end
    
    return converge
end

check_convergence (generic function with 3 methods)

In [464]:
X0 = [0, 0]
X_hist = X0[new, :]

maxit = 100
α = 0.5


convergence = false
while !convergence
    X0 -= α * ∇f(X0)
    
    X_hist = vcat(X_hist, X0[new, :])
    convergence = check_convergence(f, X_hist, maxit)
end

┌ Warning: No change observed
└ @ Main In[419]:18


In [465]:
f(X_hist[end, :]...)

0.1411200080598672

In [421]:
nsteps = 3
skip = Int(floor(length(X_hist[:, begin]) / nsteps))

contourf(xyrange, xyrange, Z, title=L"f(x,y)", c=:viridis)
plot_path!(X_hist)

## Momentum optimisation

In [446]:
X0 = [0, 0]
X_hist = X0[new, :]
maxit = 200
α = 0.05
# Play with 0.7, 0.8, 0.81
β = 0.8


convergence = false
m = ones(2)
while !convergence
    m = β * m + α * ∇f(X0)
    X0 = X0 - m
    
    X_hist = vcat(X_hist, X0[new, :])
    convergence = check_convergence(f, X_hist, maxit)
end

In [447]:
contourf(xyrange, xyrange, Z, title=L"f(x,y)", c=:viridis)
plot_path!(X_hist)

In [448]:
f(X_hist[end, :]...)

-0.9999998844353907

## Nesterov Accelerated Gradient

NAG modifies the momentum optimizer by evaluating the gradient of the function slightly ahead towards the direction of the momentum

In [480]:
X0 = [0, 0]
X_hist = X0[new, :]
maxit = 200
# Play with 0.01, 0.05
α = 0.01
# Play with 0.7, 0.8, 0.81
β = 0.7


convergence = false
m = ones(2)
while !convergence
    m = β * m + α * ∇f(X0 + β * m)
    X0 = X0 - m
    
    X_hist = vcat(X_hist, X0[new, :])
    convergence = check_convergence(f, X_hist, maxit)
end

In [481]:
f(X_hist[end, :]...)

-0.9999991673429348

In [482]:
contourf(xyrange, xyrange, Z, title=L"f(x,y)", c=:viridis)
plot_path!(X_hist)